In [1]:
import psycopg2
import json
from lst_servers import *

# Parámetros de conexión a la base de datos

json_file_path = ".\GeoJSON - Censo 2010 (Municipal).json"
with open(json_file_path, 'r', encoding='utf-8-sig') as f:
    json_content = json.load(f)

for ip in l_ips:
    conn = psycopg2.connect(
        host=ip,
        port=5432,
        database="coordenadas_mx",
        user="postgres",
        password="Shala55951254")

    cursor = conn.cursor()
    cursor.execute("DROP TABLE IF EXISTS coordenadas_mun;")

    create_table_query = """
    CREATE TABLE coordenadas_mun (
        id_edo INT,
        edo CHARACTER VARYING,
        id_mun INT,
        mun CHARACTER VARYING,
        key_edomun CHARACTER VARYING,
        geojson_mun JSONB
    );"""

    cursor.execute(create_table_query)

    # Insertar el contenido JSON en la tabla
    
    for index in enumerate(json_content['features']):
        id_edo = int(json_content['features'][index[0]]['properties']['cve_ent'])
        edo = json_content['features'][index[0]]['properties']['nom_ent']
        id_mun = int(json_content['features'][index[0]]['properties']['cve_umun'][2:])
        mun = json_content['features'][index[0]]['properties']['nom_mun']
        key_edomun = f'{id_edo}_{id_mun}'
        geometry = json_content['features'][index[0]]['geometry']
        insert_query = "INSERT INTO coordenadas_mun (id_edo, edo, id_mun, mun, key_edomun, geojson_mun ) VALUES (%s, %s, %s, %s, %s, %s);"
        cursor.execute(insert_query, (id_edo, edo, id_mun, mun, key_edomun, json.dumps(geometry),))
        
    # insert_query = "INSERT INTO coordenadas_mun (json_data) VALUES (%s);"
    # cursor.execute(insert_query, (json.dumps(json_content),))

    # guardar cambios
    conn.commit()
    # Cerrar la conexión
    cursor.close()
    conn.close()
    print(f'Servidor {ip} actualizado en coordenadas de mexico (pais)')


Servidor 192.168.1.81 actualizado en coordenadas de mexico (pais)
